In [22]:
import pandas as pd
import numpy as np
import re
import string
import calendar
import nltk 
import keras 

IMPORTING ALL ORIGINAL DATASETS

In [23]:
# AGGRESSION PARSED DATASET
ori_aggression_dataset = '/Users/churnika/Desktop/Projects/Crime_classification/dataset/aggression_parsed_dataset.csv'
ori_aggression = pd.read_csv(ori_aggression_dataset)
ori_aggression = ori_aggression.dropna()
ori_aggression.columns
ori_aggression = ori_aggression.drop(columns=['index','ed_label_0','ed_label_1', 'oh_label'])

In [24]:
# KAGGLE DATASET

ori_kaggle_dataset = '/Users/churnika/Desktop/Projects/Crime_classification/dataset/kaggle_parsed_dataset.csv'
ori_kaggle = pd.read_csv(ori_kaggle_dataset)
ori_kaggle= ori_kaggle.dropna()
ori_kaggle.columns
ori_kaggle = ori_kaggle.drop(columns=['index','oh_label', 'Date',])

In [25]:
# TOXICITY PARSED DATASET

ori_toxicity_dataset = '/Users/churnika/Desktop/Projects/Crime_classification/dataset/toxicity_parsed_dataset.csv'
ori_toxicity = pd.read_csv(ori_toxicity_dataset)
ori_toxicity = ori_toxicity.dropna()
ori_toxicity.columns
ori_toxicity = ori_toxicity.drop(columns=['index','ed_label_0', 'ed_label_1', 'oh_label'])

In [26]:
#TWITTER PARSED DATASET

ori_twitter_dataset = '/Users/churnika/Desktop/Projects/Crime_classification/dataset/twitter_parsed_dataset.csv'
ori_twitter = pd.read_csv(ori_twitter_dataset)
ori_twitter = ori_twitter.dropna()
ori_twitter.columns
ori_twitter = ori_twitter.drop(columns=['index','id','Annotation', 'oh_label'])

In [27]:
# TWITTER RACISM DATASET

ori_twit_racist_dataset = '/Users/churnika/Desktop/Projects/Crime_classification/dataset/twitter_racism_parsed_dataset.csv'
ori_twit_racist = pd.read_csv(ori_twit_racist_dataset)
ori_twit_racist = ori_twit_racist.dropna()
ori_twit_racist.columns
ori_twit_racist = ori_twit_racist.drop(columns = ['index', 'id','Annotation', 'oh_label'])

In [28]:
# TWITTER SEXISM DATASET

ori_twit_sexism_dataset = '/Users/churnika/Desktop/Projects/Crime_classification/dataset/twitter_sexism_parsed_dataset.csv'
ori_twit_sexism = pd.read_csv(ori_twit_sexism_dataset)
ori_twit_sexism = ori_twit_sexism.dropna()
ori_twit_sexism.columns
ori_twit_sexism = ori_twit_sexism.drop(columns=['index', 'id', 'Annotation', 'oh_label'])

In [29]:
# YOUTUBE PARSED DATASET

ori_utube_dataset = '/Users/churnika/Desktop/Projects/Crime_classification/dataset/youtube_parsed_dataset.csv'
ori_utube = pd.read_csv(ori_utube_dataset)
ori_utube = ori_utube.dropna()
ori_utube.columns
ori_utube = ori_utube.drop(columns=['index', 'UserIndex','Number of Comments','Number of Subscribers', 'Membership Duration', 'Number of Uploads','Profanity in UserID', 'Age', 'oh_label'])

In [30]:
frames = [ori_aggression, ori_kaggle, ori_toxicity, ori_twitter, ori_twit_racist, ori_twit_sexism]
text = pd.concat(frames)
text.columns

Index(['Text'], dtype='object')

In [31]:
msg_exp = text['Text'].str.lower()
print(len(msg_exp))

328304


In [32]:
def remove_urls(text):
    url_pattern = re.compile(r'https?://\S+|www\.\S+')
    return url_pattern.sub('', text)

msg_exp = msg_exp.apply(remove_urls)

In [33]:
# removing punctuations

def remove_punctuation(text):
    translator = str.maketrans('', '', string.punctuation)
    return text.translate(translator)

msg_exp = msg_exp.apply(remove_punctuation)

In [34]:
from nltk.corpus import stopwords

# Download the necessary NLTK data
nltk.download('punkt')
nltk.download('stopwords')

# Define the stop words
stop_words = set(stopwords.words('english'))

# Define the words to be removed
months_days = [calendar.month_name[i].lower() for i in range(1, 13)] + [calendar.day_name[i].lower() for i in range(7)]
remove_words = ["vo","n","m","c","ra","xx","r","date","hii","hi","ye","pa","xxx","p","sir","mam","good","morning","time","ur","you","status","father"]

# Define a function to remove URLs
def remove_urls(text):
    url_pattern = re.compile(r'https?://\\S+|www\\.\\S+')
    return url_pattern.sub('', text)

# Define a function to tokenize the text and remove unwanted words
def process_text(text):
    tokens = nltk.word_tokenize(text)
    tokens = [token for token in tokens if not re.match(r'http[s]?://', token)]
    tokens = [token for token in tokens if token.isalpha()]
    tokens = [token for token in tokens if token not in stop_words]
    tokens = [token for token in tokens if token not in months_days]
    tokens = [token for token in tokens if token not in remove_words]
    return tokens

# Apply the function to remove URLs
msg_exp = msg_exp.apply(remove_urls)

# Apply the function to process the text
msg_exp = msg_exp.apply(process_text)


[nltk_data] Downloading package punkt to /Users/churnika/nltk_data...
[nltk_data]   Package punkt is already up-to-date!
[nltk_data] Downloading package stopwords to
[nltk_data]     /Users/churnika/nltk_data...
[nltk_data]   Package stopwords is already up-to-date!


In [41]:
# LEMMATIZATION

from nltk.stem import WordNetLemmatizer
nltk.download('wordnet')

lemmatizer = WordNetLemmatizer()

lemmatized_tokens = [[lemmatizer.lemmatize(token) for token in tokens]for tokens in msg_exp]

[nltk_data] Downloading package wordnet to
[nltk_data]     /Users/churnika/nltk_data...
[nltk_data]   Package wordnet is already up-to-date!


In [42]:
# REMOVING RARE OR FREQUENTLY USED WORDS

from collections import Counter

freq = Counter([token for tokens in lemmatized_tokens for token in tokens])
freq_threshold = 10

lemmatized_tokens = [[token for token in tokens if freq[token] > freq_threshold] for tokens in lemmatized_tokens]

In [43]:
#REMOVING WHITESPACES

cleaned_lemmatized_tokens = [' '.join(tokens) for tokens in lemmatized_tokens]
cleaned_lemmatized_tokens = [text.split() for text in cleaned_lemmatized_tokens]

In [44]:
# Dictionary mapping abbreviations to their full forms
abbreviation_dict = {
    "don't": "do not",
    "can't": "cannot",
    "u": "you",
    "rt": "right",
    "ur":"your"
}

# Function to expand abbreviations
def expand_abbreviations(tokens):
    expanded_tokens = []
    for token in tokens:
        if token in abbreviation_dict:
            expanded_tokens.extend(abbreviation_dict[token].split())
        else:
            expanded_tokens.append(token)
    return expanded_tokens

# Expand abbreviations in cleaned_lemmatized_tokens
expanded_lemmatized_tokens = [expand_abbreviations(tokens) for tokens in cleaned_lemmatized_tokens]

In [45]:
#REMOVE ACCENTS AND DIACRITICS FROM EXPANDED_LEMMATIZED_TOKENS

from unidecode import unidecode

def remove_accents_diacritics(tokens):
    cleaned_tokens = []
    for token in tokens:
        cleaned_token = unidecode(token)
        cleaned_tokens.append(cleaned_token)
    return cleaned_tokens

expanded_lemmatized_tokens = [remove_accents_diacritics(tokens) for tokens in expanded_lemmatized_tokens]


In [46]:
# TOKENIZATION OF TEXT INTO INTEGER VALUES

from tensorflow.keras.preprocessing.text import Tokenizer

# Create a tokenizer, configured to only take into account the top-10000 most common words
tokenizer = Tokenizer(num_words=10000)

# Build the word index
tokenizer.fit_on_texts(expanded_lemmatized_tokens)

# Turn strings into lists of integer indices
sequences = tokenizer.texts_to_sequences(expanded_lemmatized_tokens)

In [47]:
from keras.preprocessing.sequence import pad_sequences

max_seq_length = 100  # or any other value based on your data

# Pad the sequences
padded_sequences = pad_sequences(sequences, maxlen=max_seq_length)

In [35]:
print(len(msg_exp))

328304


In [48]:
import numpy as np
import tensorflow as tf
from keras.models import load_model

# Assuming msg_exp is your input data
msg_exp = np.array(padded_sequences)

# Convert msg_exp to a NumPy array if it's not already
if not isinstance(msg_exp, np.ndarray):
    msg_exp = np.array(msg_exp)

# Convert to TensorFlow tensor
msg_exp_tensor = tf.convert_to_tensor(msg_exp)

# Load your models
racism_model = load_model('racism_model.h5')
sexism_model = load_model('sexism_model.h5')

# Use your models to predict
racism_preds = racism_model.predict(msg_exp_tensor)
sexism_preds = sexism_model.predict(msg_exp_tensor)

# Perform further processing as needed


10260/10260 ━━━━━━━━━━━━━━━━━━━━ 36s 4ms/step
10260/10260 ━━━━━━━━━━━━━━━━━━━━ 36s 3ms/step


In [49]:
racism_labels = np.where(racism_preds > 0.5, 'Racist', 'Not Racist')
sexism_labels = np.where(sexism_preds > 0.5, 'Sexist', 'Not Sexist')

print(racism_labels)
print(sexism_labels)

[['Not Racist']
 ['Not Racist']
 ['Not Racist']
 ...
 ['Not Racist']
 ['Not Racist']
 ['Not Racist']]
[['Not Sexist']
 ['Sexist']
 ['Not Sexist']
 ...
 ['Not Sexist']
 ['Sexist']
 ['Not Sexist']]


In [50]:
for label in racism_labels:
    print(label)

['Not Racist']
['Not Racist']
['Not Racist']
['Not Racist']
['Not Racist']
['Not Racist']
['Not Racist']
['Not Racist']
['Not Racist']
['Not Racist']
['Not Racist']
['Not Racist']
['Not Racist']
['Not Racist']
['Not Racist']
['Not Racist']
['Not Racist']
['Not Racist']
['Not Racist']
['Not Racist']
['Not Racist']
['Not Racist']
['Not Racist']
['Not Racist']
['Not Racist']
['Not Racist']
['Racist']
['Not Racist']
['Not Racist']
['Not Racist']
['Not Racist']
['Not Racist']
['Not Racist']
['Racist']
['Not Racist']
['Not Racist']
['Not Racist']
['Racist']
['Not Racist']
['Racist']
['Not Racist']
['Not Racist']
['Racist']
['Not Racist']
['Not Racist']
['Not Racist']
['Not Racist']
['Not Racist']
['Not Racist']
['Not Racist']
['Not Racist']
['Not Racist']
['Racist']
['Not Racist']
['Not Racist']
['Not Racist']
['Not Racist']
['Not Racist']
['Not Racist']
['Not Racist']
['Not Racist']
['Not Racist']
['Not Racist']
['Not Racist']
['Not Racist']
['Not Racist']
['Not Racist']
['Not Racist']
['No